In [86]:
import numpy as np
from scipy.stats import invgamma
from plotly.subplots import make_subplots
import plotly.graph_objs as go
import time
import plotly.io as pio
from scipy import stats
from urllib.request import urlopen 
import pywikibot
import concurrent
import json
from collections import deque
pio.renderers.default = 'iframe'

L'objectif de ce notebook est de trouver le chemin le plus rapide (au sens du temps de chargement) entre deux pages wikipedia données. Un chemin entre deux pages est une succession d'articles wikipedia où l'article d'indice n était référencé dans l'article d'indice n-1 en tant qu'hyperlien.

Le temps de chargement des pages wikipedia peut beaucoup varier selon la taille de la page et les documents qu'elle contient (x5-x10 entre un article court et de très gros articles comme celui des Etats-Unis en anglais). Cela implique donc que le chemin le plus rapide (au sens du temps de chargement des pages) n'est pas forcément celui avec le moins d'articles. Passer par un chemin plus long, constitué d'articles moins populaires (donc au temps de chargement plus faible) peut s'avérer pertinent.

On peut également remarquer que le temps de chargement de chacun des articles a une variance important. Le constat est donc le même pour un chemin constitué de plusieurs articles. Trouver le chemin le plus rapide n'est donc pas forcément facile. Ici, on le résout grâce à l'algorithme de thompson sampling qui propose une policy pour trouver le chemin le plus rapide tout en minimisant la latence totale.

# Build wikipedia graph

La première étape est de construire un graph de wikipedia où les noeuds sont des articles. Chaque article est connecté au articles qu'il cite dans son texte. 

In [87]:
def extract_linked_pages(article_title, language='en'):
    site = pywikibot.Site(language, 'wikipedia')
    page = pywikibot.Page(site, article_title)
    
    linked_pages = page.linkedPages()
    
    linked_article_titles = [linked_page.title() for linked_page in linked_pages \
                             if (linked_page.namespace() == 0) and ('identifier' not in linked_page.title()) and (linked_page.exists())]
    return linked_article_titles

In [88]:
graph = {}
max_graph_nodes = 1000
start_page = "Thompson sampling" 
max_workers = 11

current_pages = [start_page]
waiting_nodes = deque()
nb_iter = max_graph_nodes // max_workers

for i in tqdm(range(nb_iter)):
    with concurrent.futures.ThreadPoolExecutor(max_workers) as executor:
        page_links = list(executor.map(extract_linked_pages, current_pages))
    
    graph.update({current_pages[i]: page_links[i] for i in range(len(page_links))})
    page_links = [l for links in page_links for l in links if l not in graph]
    waiting_nodes += page_links

    current_pages = [waiting_nodes.popleft() for _ in range(max_workers)]

  0%|          | 0/90 [00:00<?, ?it/s]

In [89]:
def remove_unknown_neibghors_nodes(graph):
    known_neibghors_nodes = list(graph.keys())
    pruned_graph = {key:[v for v in value if v in known_neibghors_nodes] for key, value in graph.items()}
    return pruned_graph

In [90]:
graph = remove_unknown_neibghors_nodes(graph)

In [96]:
GRAPH_PATH = "graph.json"
with open(GRAPH_PATH, "w") as outfile: 
    json.dump(graph, outfile)

In [92]:
graph

{'Thompson sampling': ['Biometrika',
  'Causality',
  'Exploration-exploitation dilemma',
  'Heuristic',
  'Ian Clarke (computer scientist)',
  'Indicator function',
  'Markov decision process',
  'Mathematics of Operations Research',
  'Multi-armed bandit',
  'Probability matching',
  'William R. Thompson'],
 'Biometrika': ['Academic publishing',
  'Animal',
  'Annals of Statistics',
  'Annals of the Institute of Statistical Mathematics',
  'Anthony C. Davison',
  'BIOSIS Previews',
  'Biological Abstracts',
  'Biometrical Journal',
  'Biometrics (journal)',
  'Biostatistics',
  'Biostatistics (journal)',
  'Brazilian Journal of Probability and Statistics',
  'CAB Abstracts',
  'Charles Darwin',
  'Charles Davenport',
  'Chilean Journal of Statistics',
  'Clarivate Analytics',
  'Communications in Statistics',
  'Comparison of statistics journals',
  'Cross-multiplication',
  'Current Contents',
  'Current Index to Statistics',
  'David Cox (statistician)',
  'David Hinkley',
  'Delay

# Fonctions pour estimer la latence

In [2]:
def estimate_url_latency(url):
    website = urlopen(url) 
    open_time = time.time()  
    output = website.read() 
    close_time = time.time() 
    website.close() 
    return (close_time - open_time) * 1000

def get_url_from_article_title(title):
    site = pywikibot.Site('en', 'wikipedia')
    page = pywikibot.Page(site, title)
    url = page.full_url()
    return url

## Bandits Gaussien

Le temps de chargement de chaque chemin est modélisée par une loi normale. Le conjugate prior de la loi normale de moyenne et de variance inconnue est la loi Normale Inverse Gamma (on se sert donc de cette loi pour modéliser le prior et le posterior). 

In [204]:
class GaussianArm :
    def __init__(self, initial_params, path, num_observations=1):
        
        self.µ, self.v, self.α, self.β = initial_params
        self.path = path
        self.var = self.β / (self.α + 1)
        self.num_observations = num_observations
        self.N = 0
        self.observations_list = []

    def sample_prior(self):
        mean = self.µ
        std = np.sqrt(invgamma(self.α, self.β).rvs(1)[0] / (self.v))
        return np.random.normal(mean, std, 1)

    def get_observation(self):
        path_urls = [get_url_from_article_title(title) for title in self.path]
        path_urls *= self.num_observations

        max_workers = 11
        with concurrent.futures.ThreadPoolExecutor(max_workers) as executor:
            url_latencies = list(executor.map(estimate_url_latency, path_urls))
        url_latencies = np.array_split(url_latencies, self.num_observations)
        path_latencies = np.sum(url_latencies, axis=-1)
        return path_latencies

    def compute_posterior(self, observations):

        self.µ = ((self.µ * self.v) + self.num_observations * np.mean(observations)) / (self.v + self.num_observations)
        self.v += self.num_observations
        self.α += self.num_observations / 2 
        self.β += np.std(observations) * 0.5 * self.num_observations + ((self.num_observations * self.v) / (self.num_observations + self.N)) * (((np.mean(observations) - self.µ)**2)/2) 

        self.var = self.β / (self.α + 1 + 1/2)

    def get_params(self):
        return self.µ, self.var ** 0.5

In [205]:
class MultiArmedBandit():
    def __init__(self, arms, theoretical_params=None):
        self.arms = arms
        self.n_iter = 0
        self.latencies = []

    def sample_priors(self):
        return [arm.sample_prior() for arm in self.arms]
        
    def compute_posteriors(self, arm_index, observation):
        self.arms[arm_index].compute_posterior(observation)
        self.latencies.append(observation)
        self.n_iter += 1

    def get_params(self):
        return [arm.get_params() for arm in self.arms]

    def get_best_path(self):
        path_average_time = [arm.µ for arm in self.arms]
        best_path_index = np.argmin(path_average_time)
        return self.arms[best_path_index].path
    
    def show(self):
        fig = make_subplots(rows=1, cols=2, subplot_titles=["Paths latency distributions", "Cumulative Latency"])
    
        for i, (mean, std) in enumerate(self.get_params()):
            x = np.linspace(mean - 4*std, mean + 4*std, 200)
            gaussian_pdf = stats.norm.pdf(x, mean, std)
            
            fig.add_trace(go.Scatter(x=x,
                                     y=gaussian_pdf,
                                     mode='lines',
                                     name=f"{i} - Mean={round(mean, 2)}, Std={round(std, 2)} - Num tries {self.arms[i].v - 1}"),
                         row=1, col=1)

        fig.add_trace(go.Scatter(x=list(range(len(self.latencies))), y=np.cumsum(self.latencies), mode='lines', name='Cumulative Latency'), row=1, col=2)
    
        fig.update_layout(title_text=f"Itération : {self.n_iter}")
        fig.show()
        

# Algorithme de Depth First Search

Pour obtenir une liste des chemins reliant deux nodes, on se sert de l'algorithme de Depth First Search. Il permet d'obtenir tous les chemins entre deux nodes d'un graph d'une longueur maximale = max_depth. 

In [160]:
def dfs(graph, start, end, max_depth, path=None):
    if path is None:
        path = []
    path = path + [start]

    if start == end:
        return [path]

    if max_depth <= 0:
        return []

    if start not in graph:
        return []

    paths = []
    for node in graph[start]:
        if node not in path:
            new_paths = dfs(graph, node, end, max_depth - 1, path)
            for new_path in new_paths:
                paths.append(new_path)
    return paths

In [111]:
with open(GRAPH_PATH) as graph:
  graph = json.loads(graph.read())

In [112]:
graph

{'Thompson sampling': ['Biometrika',
  'Causality',
  'Exploration-exploitation dilemma',
  'Heuristic',
  'Ian Clarke (computer scientist)',
  'Indicator function',
  'Markov decision process',
  'Mathematics of Operations Research',
  'Multi-armed bandit',
  'Probability matching',
  'William R. Thompson'],
 'Biometrika': ['Academic publishing',
  'Animal',
  'Annals of Statistics',
  'Annals of the Institute of Statistical Mathematics',
  'Anthony C. Davison',
  'BIOSIS Previews',
  'Biological Abstracts',
  'Biometrical Journal',
  'Biometrics (journal)',
  'Biostatistics',
  'Biostatistics (journal)',
  'Brazilian Journal of Probability and Statistics',
  'CAB Abstracts',
  'Charles Darwin',
  'Charles Davenport',
  'Chilean Journal of Statistics',
  'Clarivate Analytics',
  'Communications in Statistics',
  'Comparison of statistics journals',
  'Cross-multiplication',
  'Current Contents',
  'Current Index to Statistics',
  'David Cox (statistician)',
  'David Hinkley',
  'Delay

# Thompson sampling

On peut maintenant appliquer l'algorithme de thompson sampling pour trouver le chemin le plus court entre deux articles que l'on a choisit (pour ne pas avoir une quantité gigantesque de chemin, il vaut mieux réduire la max_depth ou alors choisir des nodes de départ et d'arrivée peu populaires).

In [213]:
start_node = 'Thompson sampling'
end_node = 'Albert Einstein'
paths = dfs(graph, start_node, end_node, max_depth=3)
print(f"Number of paths : {len(paths)}")
#print("Chemins possibles entre", start_node, "et", end_node, ":", paths)

Number of paths : 83


In [214]:
arms = [GaussianArm(initial_params=(500, 1, 1, 10000), path=paths[i], num_observations=1) for i in range(len(paths))]
mab = MultiArmedBandit(arms)

num_iters = 1000
eval_iters = 50

for i in tqdm(range(num_iters)):
    sampled_values = mab.sample_priors()
    best_arm_index = np.argmin(sampled_values)
    observation = mab.arms[best_arm_index].get_observation()
    mab.compute_posteriors(best_arm_index, observation)
    #time.sleep(1)
    if i % eval_iters == eval_iters - 1:
        print(f"At iteration {i}, the best path is {mab.get_best_path()}")
        time.sleep(1)
        mab.show()

  0%|          | 0/1000 [00:00<?, ?it/s]

At iteration 49, the best path is ['Thompson sampling', 'Causality', 'Anthropic principle', 'Albert Einstein']


URLError: <urlopen error [Errno 8] nodename nor servname provided, or not known>

In [178]:
x = np.arange(8.0)
np.array_split([i for i in range(8)], 3)

[array([0., 1., 2.]), array([3., 4., 5.]), array([6., 7.])]

# Djikstra

On peut comparer le chemin trouvé par un algorithme de djikstra (après avoir évalué le temps de chargement de tous les noeuds du graph une seule fois) et celui trouvé par l'algorithme de thompson sampling . 

In [129]:
def dijkstra(graph, start, end, latencies):
    # Initialisation des distances à l'infini pour tous les noeuds sauf le départ
    distances = {node: float('inf') for node in graph}
    distances[start] = 0
    
    # Initialisation de la file de priorité avec le noeud de départ
    queue = [(0, start)]
    
    # Initialisation du dictionnaire de prédécesseurs pour reconstruire le chemin
    predecessors = {node: None for node in graph}
    
    while queue:
        # Récupération du noeud actuel et de sa distance depuis le début
        current_distance, current_node = heapq.heappop(queue)
        
        # Si on atteint le noeud cible, on reconstruit le chemin et on retourne la distance et le chemin
        if current_node == end:
            path = []
            while current_node is not None:
                path.append(current_node)
                current_node = predecessors[current_node]
            return distances, list(reversed(path))
        
        # Si la distance actuelle est supérieure à celle déjà connue, on l'ignore
        if current_distance > distances[current_node]:
            continue
        
        # Parcours des voisins du noeud actuel
        for neighbor in graph[current_node]:
            weight = latencies[neighbor]
            distance = current_distance + weight
            
            # Si la distance jusqu'au voisin est plus courte que celle connue jusqu'à présent, on la met à jour
            if distance < distances[neighbor]:
                distances[neighbor] = distance
                predecessors[neighbor] = current_node
                heapq.heappush(queue, (distance, neighbor))
    
    # Si aucun chemin n'a été trouvé, retourner None
    return float('inf'), None

In [130]:
import concurrent.futures
from tqdm import tqdm

def estimate_articles_latency_once(node_list):
    max_workers = 11

    latency_estimates = {}
    with concurrent.futures.ThreadPoolExecutor(max_workers) as executor:
        # Chunk the node_list into batches of max_workers titles
        chunks = [node_list[i:i + max_workers] for i in range(0, len(node_list), max_workers)]

        # Iterate over each chunk
        for chunk in tqdm(chunks):
            # Map the estimate_url_latency function to each title in the chunk
            urls = list(executor.map(get_url_from_article_title, chunk))
            latencies = list(executor.map(estimate_url_latency, urls))
            

            # Aggregate the latencies into the latency_estimates dictionary
            for title, latency in zip(chunk, latencies):
                latency_estimates[title] = latency

    return latency_estimates


In [138]:
from tqdm.notebook import tqdm
graph_nodes = list(graph.values()) + [list(graph.keys())]
unique_nodes = list(set([n for nodes in graph_nodes for n in nodes]))
print(f'Number of unique nodes : {len(unique_nodes)}')
latencies = estimate_articles_latency_once(unique_nodes)

Number of unique nodes : 977


  0%|          | 0/89 [00:00<?, ?it/s]

KeyboardInterrupt: 

In [134]:
start_node = 'Thompson sampling'
end_node = 'Cosmology'
distances, optimal_path = dijkstra(graph, start_node, end_node, latencies)
print(f"Distances from node {start_node} to {end_node} : {distances[end_node]}")

Distances from node Thompson sampling to Cosmology : 1193.0229663848877


In [135]:
print(f"The optimal path found by Djikstra is : {optimal_path}")
print(f"The optimal path found by Thompson sampling is : {mab.get_best_path()}")

The optimal path found by Djikstra is : ['Thompson sampling', 'Mathematics of Operations Research', 'Outline of academic disciplines', 'Cosmology']
The optimal path found by Thompson sampling is : ['Thompson sampling', 'Causality', 'Cosmology']
